In [1]:
%%time

import requests
from bs4 import BeautifulSoup
import pandas as pd

from geopy.geocoders import Nominatim
import folium

pd.set_option("display.max_columns",None)
pd.set_option("display.max_rows",None)
import requests
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service as ChromeService
from webdriver_manager.chrome import ChromeDriverManager
import re
import time
from selenium.webdriver.chrome.options import Options
import pandas as pd

# URL to fetch data
URL = "https://rejstriky.msmt.cz/rejskol/LoginPage.aspx"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

# Extracting options for zrizovatel and druhy_skol
select = soup.find(id='cmdSpravniUrad_dD')
options = select.find_all('option')
zrizovatel_moznosti = [option.text.strip() for option in options]

vyber = soup.find("select", {"name": "ctl38"})
moznosti = vyber.find_all("option")
druhy_skol_moznosti = [moznost["value"] for moznost in moznosti]

#len(zrizovatel_moznosti)

#https://chromedriver.chromium.org/downloads

# Setting up headless Chrome options
options = Options()
options.add_argument('--headless') # <---- headless browser
######################################################################
#stažení všech IZO čísel všech škol náležejících k jednotlivým zřizovatelům
zriz = zrizovatel_moznosti[1:]  #<--- Zřizovatelů je celkem 244

for z in zriz:
    izo_vse=[]
    for v in druhy_skol_moznosti[1:]:
        service = ChromeService(executable_path='/home/pavlina/Stažené/chromedriver-linux64/chromedriver-linux64/chromedriver')
        driver = webdriver.Chrome(service=service, options=options)
        driver.get("https://rejstriky.msmt.cz/rejskol/LoginPage.aspx")

        #time.sleep(3)
        school_type_select = Select(driver.find_element(By.NAME, "cmdSpravniUrad_dD"))
        school_type_select.select_by_visible_text(z)

        druh_skoly_select = Select(driver.find_element(By.NAME, "ctl38"))
        druh_skoly_select.select_by_value(v)

        driver.find_element(By.NAME, "btnVybrat").click()

        driver.implicitly_wait(2)

        izo = []

        rows = driver.find_elements(By.TAG_NAME, "tr") 
        for row in rows[1:]:  # Skip the first row (table header)
            cols = row.find_elements(By.TAG_NAME, "td")
            try:
                vysl=""
                naslo = re.findall("\d{9}",str(cols[0].text))
                for e in naslo:
                    vysl += "" + e
                if vysl == str(cols[0].text):
                    if vysl:
                        izo.append(str(cols[0].text))
            except:
                print(f"{v}")

        try:    
            pocet_stranek = int(str(rows[1].text)[-10])

            s=2    
            while s <= pocet_stranek:
                # Scrape data from the remaining pages
                driver.find_element(By.NAME, "btnNext2").click()
                driver.implicitly_wait(2)

                rows = driver.find_elements(By.TAG_NAME, "tr")
                for row in rows[1:]:  
                    cols = row.find_elements(By.TAG_NAME, "td")
                    try:
                        #file1.write(cols[0].text)
                        vysl=""
                        naslo = re.findall("\d{9}",str(cols[0].text))
                        for e in naslo:
                            vysl += "" + e
                        if vysl == str(cols[0].text):
                            if vysl:
                                izo.append(str(cols[0].text))
                    except:
                        print(f"{v}-{s}")
                s=s+1

            izo_vse.append(izo)
            #print(izo)
            print(len(izo))
            driver.find_element(By.NAME, "btnZpetNaVyber2").click()
        except:
            print("nic tu není")
        print("___")

    #file1.close()    

    # Close the browser
    #driver.close()
    driver.quit()

    flat_list = [item for sublist in izo_vse for item in sublist]
    print(f"celk. pocet IZO čísel: {len(flat_list)}")

    cisla= pd.DataFrame(flat_list, columns=["IZO"])
    cisla.to_csv(f"{z}.csv", index=False, sep="#")
    
    
    #####################################################################################
    #2 stažení informací ke každé škole a vytvoření tabulky
    service = ChromeService(executable_path='/home/pavlina/Stažené/chromedriver-linux64/chromedriver-linux64/chromedriver')
    driver = webdriver.Chrome(service=service, options=options)
    driver.get("https://rejstriky.msmt.cz/rejskol/LoginPage.aspx")

    uplne_vse = []
    for k in list(cisla["IZO"].unique()):
        search_box = driver.find_element(By.XPATH, '//*[@id="ctl17_txt"]')   #ctl17_txt
        search_box.send_keys(k) 
        search_button = driver.find_element(by=By.NAME, value="btnVybrat")
        search_button.click()

        odkazy = driver.find_elements(By.XPATH, "//td[@class='titbgr']/a[@href]")

        for odkaz in odkazy:
            if "PravOsoba" in odkaz.get_attribute("href"):
                prav_osoba = odkaz

        prav_osoba.click()

        vse = []

        nazev = driver.find_element(By.ID, "lblJmenoPravOsoby")
        adresa = driver.find_element(By.ID, "lblAdresa")
        ico = driver.find_element(By.ID, "lblICO")
        izo = driver.find_element(By.ID, "lblRedIzo")
        reditel = driver.find_element(By.ID, "lblReditel")
        pravni_forma = driver.find_element(By.ID, "lblPravniForma")
        try:
            zrizovatel = driver.find_element(By.ID, "lblZrizovatel")
        except:
            zrizovatel = "nufin"

        vse.append(nazev.text)
        vse.append(adresa.text)
        vse.append(ico.text)
        vse.append(izo.text)
        vse.append(reditel.text)
        vse.append(pravni_forma.text)
        try:
            vse.append(zrizovatel.text)
        except:
            vse.append("Není uveden")

        tabulka = driver.find_element(By.ID, "DataListSeznam") #//*[@id="DataListSeznam"] 
        vse_v_tabulce = tabulka.find_elements(By.CLASS_NAME, "titmodry")
        for i in vse_v_tabulce:
            vse.append(i.text)
        uplne_vse.append(vse)

        zpet = driver.find_element(By.XPATH, "//*[@id='btnZpet']")
        zpet.click()

        driver.find_element(By.NAME, "btnZpetNaVyber2").click()

        search_box = driver.find_element(By.ID, "ctl17_txt")
        search_box.clear()
    driver.close()

    vysledek = pd.DataFrame(uplne_vse)
    vysledek["zrizovatel_dropdown"] = f'{z.split(", ")[1]}'
    vysledek.to_csv(f"{z}_vysledek.csv", index=False, sep="#", encoding="utf-8")
    print(f"Uložen soubor {z}_vysledek.csv") 
    #####################################################################################
    #3. Nalezení GPS souřadnic jednotlivých škol dle jejich adresy ve sloupci "adresa"
    # Sample DataFrame with addresses
    data = vysledek[1]
    df = pd.DataFrame(data)

    # Initialize the geolocator
    geolocator = Nominatim(user_agent="address_locator")

    # Function to geocode an address
    def geocode_address(address):
        try:
            location = geolocator.geocode(address)
            return (location.latitude, location.longitude)
        except:
            return None

    # Apply the function to the DataFrame
    df['Coordinates'] = df[1].apply(geocode_address)
    df = df.Coordinates
    print(f"Získány GPS souřadnice")
    
    result = vysledek.join(df)
    result.to_csv(f"{z}_vysledek_f.csv", index=False, sep="#", encoding="utf-8")
    print(f"Uložen soubor {z}_vysledek_f.csv") 
    print()
    
print(result.shape)
print(result.Coordinates.isna().sum())

A
7
___
B
B-2
B-3
B-4
B-5
49
___
C
C-2
C-3
29
___
D
1
___
E
nic tu není
___
F
1
___
F10
1
___
F20
nic tu není
___
G
G-2
11
___
G11
1
___
G12
1
___
G21
8
___
G22
5
___
G40
1
___
H
9
___
H10
nic tu není
___
H21
8
___
H22
1
___
J
J-2
J-3
J-4
J-5
J-6
58
___
J11
1
___
J12
J12-2
J12-3
28
___
J13
J13-2
J13-3
25
___
J14
J14-2
12
___
J21
J21-2
J21-3
29
___
K
9
___
K10
nic tu není
___
K20
9
___
L
L-2
L-3
L-4
L-5
L-6
L-7
66
___
L11
L11-2
L11-3
L11-4
L11-5
L11-6
L11-7
64
___
L12
nic tu není
___
L13
9
___
L15
nic tu není
___
L19
nic tu není
___
M
nic tu není
___
M10
nic tu není
___
M20
nic tu není
___
M30
nic tu není
___
M40
nic tu není
___
M49
nic tu není
___
M50
nic tu není
___
M60
nic tu není
___
M79
nic tu není
___
celk. pocet IZO čísel: 443
Uložen soubor A90100, MŠMT_vysledek.csv
Získány GPS souřadnice
Uložen soubor A90100, MŠMT_vysledek_f.csv

A
1
___
B
nic tu není
___
C
5
___
D
nic tu není
___
E
4
___
F
nic tu není
___
F10
nic tu není
___
F20
nic tu není
___
G
1
___
G11
nic tu není
___
G12
n

K20
6
___
L
L-2
L-3
L-4
L-5
L-6
L-7
L-8
78
___
L11
L11-2
L11-3
L11-4
L11-5
47
___
L12
2
___
L13
L13-2
L13-3
L13-4
38
___
L15
2
___
L19
nic tu není
___
M
3
___
M10
1
___
M20
nic tu není
___
M30
2
___
M40
nic tu není
___
M49
nic tu není
___
M50
nic tu není
___
M60
nic tu není
___
M79
nic tu není
___
celk. pocet IZO čísel: 527
Uložen soubor B52000, KÚ Královéhradeckého kraje_vysledek.csv
Získány GPS souřadnice
Uložen soubor B52000, KÚ Královéhradeckého kraje_vysledek_f.csv

A
A-2
17
___
B
B-2
B-3
26
___
C
C-2
C-3
C-4
C-5
C-6
C-7
C-8
74
___
D
1
___
E
5
___
F
5
___
F10
3
___
F20
2
___
G
G-2
G-3
28
___
G11
1
___
G12
nic tu není
___
G21
G21-2
G21-3
25
___
G22
4
___
G40
2
___
H
H-2
H-3
H-4
35
___
H10
nic tu není
___
H21
2
___
H22
H22-2
H22-3
H22-4
33
___
J
7
___
J11
6
___
J12
nic tu není
___
J13
nic tu není
___
J14
nic tu není
___
J21
1
___
K
5
___
K10
2
___
K20
4
___
L
L-2
L-3
L-4
L-5
L-6
60
___
L11
L11-2
L11-3
L11-4
L11-5
41
___
L12
nic tu není
___
L13
L13-2
L13-3
23
___
L15
2
___
L19
nic tu

K
nic tu není
___
K10
nic tu není
___
K20
nic tu není
___
L
L-2
L-3
22
___
L11
L11-2
L11-3
21
___
L12
nic tu není
___
L13
5
___
L15
nic tu není
___
L19
nic tu není
___
M
nic tu není
___
M10
nic tu není
___
M20
nic tu není
___
M30
nic tu není
___
M40
nic tu není
___
M49
nic tu není
___
M50
nic tu není
___
M60
nic tu není
___
M79
nic tu není
___
celk. pocet IZO čísel: 96
Uložen soubor D11030, ÚMČ Praha 3_vysledek.csv
Získány GPS souřadnice
Uložen soubor D11030, ÚMČ Praha 3_vysledek_f.csv

A
A-2
A-3
24
___
B
B-2
B-3
22
___
C
1
___
D
nic tu není
___
E
nic tu není
___
F
nic tu není
___
F10
nic tu není
___
F20
nic tu není
___
G
G-2
G-3
22
___
G11
nic tu není
___
G12
nic tu není
___
G21
G21-2
G21-3
22
___
G22
2
___
G40
nic tu není
___
H
nic tu není
___
H10
nic tu není
___
H21
nic tu není
___
H22
nic tu není
___
J
nic tu není
___
J11
nic tu není
___
J12
nic tu není
___
J13
nic tu není
___
J14
nic tu není
___
J21
nic tu není
___
K
nic tu není
___
K10
nic tu není
___
K20
nic tu není
___
L
L-2
L-

J
nic tu není
___
J11
nic tu není
___
J12
nic tu není
___
J13
nic tu není
___
J14
nic tu není
___
J21
nic tu není
___
K
nic tu není
___
K10
nic tu není
___
K20
nic tu není
___
L
L-2
L-3
28
___
L11
L11-2
L11-3
28
___
L12
nic tu není
___
L13
4
___
L15
nic tu není
___
L19
nic tu není
___
M
nic tu není
___
M10
nic tu není
___
M20
nic tu není
___
M30
nic tu není
___
M40
nic tu není
___
M49
nic tu není
___
M50
nic tu není
___
M60
nic tu není
___
M79
nic tu není
___
celk. pocet IZO čísel: 116
Uložen soubor D11120, ÚMČ Praha 12_vysledek.csv
Získány GPS souřadnice
Uložen soubor D11120, ÚMČ Praha 12_vysledek_f.csv

A
A-2
A-3
23
___
B
B-2
11
___
C
nic tu není
___
D
nic tu není
___
E
nic tu není
___
F
nic tu není
___
F10
nic tu není
___
F20
nic tu není
___
G
G-2
12
___
G11
1
___
G12
nic tu není
___
G21
G21-2
11
___
G22
2
___
G40
nic tu není
___
H
nic tu není
___
H10
nic tu není
___
H21
nic tu není
___
H22
nic tu není
___
J
nic tu není
___
J11
nic tu není
___
J12
nic tu není
___
J13
nic tu není
___

KeyboardInterrupt: 

In [2]:
#spojení všech tabulek dohromady
import glob
from IPython.display import display

files = glob.glob("*_vysledek_f.csv")
dfs = [pd.read_csv(f, sep="#") for f in files]

celk_df = pd.concat(dfs,ignore_index=True, axis = 0)
#print(cisla["IZO"].nunique())
print(celk_df.shape)

column_to_move = 'Coordinates'
cols = [col for col in celk_df.columns if col != column_to_move]
celk_df = celk_df[cols + [column_to_move]]

column_to_move = 'zrizovatel_dropdown'
cols = list(celk_df.columns)
cols.remove(column_to_move)
cols.insert(-1, column_to_move)
celk_df = celk_df[cols] # Reorder the DataFrame

display(celk_df.head(3))

#####################################################################

celk_df.rename(columns={"0":"nazev",
                       "1":"adresa",
                       "2":"ico",
                        "3":"izo",
                        "4":"reditel",
                        "5":"pravni_forma",
                        "6":"zrizovatel",
                        "7":"id2",
                        "8":"typ2",
                        "9":"nazev2",
                        "10":"obec2",
                        "11":"ulice2",
                        "12":"cislo_popisne2",
                        "13":"cislo_orientacni2",
                        "14":"mestska_cast2",
                        "15":"psc2",
                        "16":"vyucovaci_jazyk2",
                        "17":"kapacita2",
                        "18":"platnost_zarizeni2"
                       }, inplace = True)


str_list = ['id', 'typ', 'nazev', 'obec', 'ulice', 'cislo_popisne', 'cislo_orientacni', 'mestska_cast', 'psc', 'vyucovaci_jazyk', 'kapacita', 'platnost_zarizeni']
num_list = list(range(19, celk_df.shape[1]-2))

suffix = 3
dict_out = {}
for num in num_list:
    str_index = (num - 19) % len(str_list)
    dict_out[str(num)] = str_list[str_index] + str(suffix)
    if str_index == len(str_list) - 1:
        suffix += 1

#print(dict_out)
celk_df = celk_df.rename(columns=dict_out)

celk_df.to_csv("celk_df.csv", index=False, sep="#", encoding="utf-8")

display(celk_df.head(3))
print(celk_df.shape)

(2987, 117)


0  \
0  Základní škola a Mateřská škola Trivium Plus o...   
1  Základní škola a Mateřská škola při Fakultní n...   
2  Mateřská škola, základní škola a střední škola...   

                                                   1         2          3  \
0                             č.p. 2, 518 01 Dobřany  64829804  600001491   
1  Sokolská 581, Nový Hradec Králové, 500 03 Hrad...  70837554  600023915   
2  Nerudova 1180/28, Pražské Předměstí, 500 02 Hr...  25262165  600023940   

                       4                              5  \
0       Mgr. Jan Grulich    obecně prospěšná společnost   
1  Mgr. Blanka Kovandová         příspěvková organizace   
2    Mgr. Monika Bourová  společnost s ručením omezeným   

                                                   6          7    8  \
0                                        Není uveden  108024181  B00   
1  Královéhradecký kraj, Pivovarské náměstí 1245/...  102754713  A00   
2                                        Není uveden   48162485  B00   

                9              10        11      12    13  \
0  Základní škola         Dobřany       NaN     2.0   NaN   
1  Mateřská škola  Hradec Králové  Sokolská   581.0   NaN   
2  Základní škola  Hradec Králové  Nerudova  1180.0  28.0   

                    14       15   16   17      18           19   20  \
0              Dobřany  51801.0  NaN  250  Platné  150048408.0  G21   
1  Nový Hradec Králové  50003.0  NaN   30  Platné  102078297.0  B00   
2    Pražské Předměstí  50002.0  NaN   70  Platné  110011473.0  C00   

               21              22        23      24   25                   26  \
0  Školní družina         Dobřany       NaN     2.0  NaN              Dobřany   
1  Základní škola  Hradec Králové  Sokolská   581.0  NaN  Nový Hradec Králové   
2   Střední škola  Hradec Králové   Lidická  1175.0  2.0    Slezské Předměstí   

        27   28  29      30           31   32              33              34  \
0  51801.0  NaN  47  Platné  150048416.0  G22     Školní klub         Dobřany   
1  50003.0  NaN  60  Platné  181106825.0  G22     Školní klub  Hradec Králové   
2  50002.0  NaN  44  Platné  110011481.0  G21  Školní družina  Hradec Králové   

         35      36    37                   38       39  40  41      42  \
0       NaN     2.0   NaN              Dobřany  51801.0 NaN  66  Platné   
1  Sokolská   581.0   NaN  Nový Hradec Králové  50003.0 NaN  60  Platné   
2  Nerudova  1180.0  28.0    Pražské Předměstí  50002.0 NaN  40  Platné   

            43   44              45              46        47      48    49  \
0  110036751.0  L11  Školní jídelna         Dobřany       NaN     2.0   NaN   
1          NaN  NaN             NaN             NaN       NaN     NaN   NaN   
2  150061790.0  G22     Školní klub  Hradec Králové  Nerudova  1180.0  28.0   

                  50       51  52   53      54           55   56  \
0            Dobřany  51801.0 NaN  220  Platné  181042096.0  A00   
1                NaN      NaN NaN  NaN     NaN          NaN  NaN   
2  Pražské Předměstí  50002.0 NaN   24  Platné  110011490.0  L11   

               57              58        59      60    61                 62  \
0  Mateřská škola          Bystré       NaN    82.0   NaN             Bystré   
1             NaN             NaN       NaN     NaN   NaN                NaN   
2  Školní jídelna  Hradec Králové  Nerudova  1180.0  28.0  Pražské Předměstí   

        63  64   65      66           67   68                        69  \
0  51801.0 NaN   30  Platné  181042100.0  L13  Školní jídelna - výdejna   
1      NaN NaN  NaN     NaN          NaN  NaN                       NaN   
2  50002.0 NaN  120  Platné  181004917.0  A00            Mateřská škola   

               70      71      72   73                 74       75  76   77  \
0          Bystré     NaN    82.0  NaN             Bystré  51801.0 NaN   35   
1             NaN     NaN     NaN  NaN                NaN      NaN NaN  NaN   
2  Hradec Králové  Uhelná  1142.0  1.0  Slezské Předměstí  50

nazev  \
0  Základní škola a Mateřská škola Trivium Plus o...   
1  Základní škola a Mateřská škola při Fakultní n...   
2  Mateřská škola, základní škola a střední škola...   

                                              adresa       ico        izo  \
0                             č.p. 2, 518 01 Dobřany  64829804  600001491   
1  Sokolská 581, Nový Hradec Králové, 500 03 Hrad...  70837554  600023915   
2  Nerudova 1180/28, Pražské Předměstí, 500 02 Hr...  25262165  600023940   

                 reditel                   pravni_forma  \
0       Mgr. Jan Grulich    obecně prospěšná společnost   
1  Mgr. Blanka Kovandová         příspěvková organizace   
2    Mgr. Monika Bourová  společnost s ručením omezeným   

                                          zrizovatel        id2 typ2  \
0                                        Není uveden  108024181  B00   
1  Královéhradecký kraj, Pivovarské náměstí 1245/...  102754713  A00   
2                                        Není uveden   48162485  B00   

           nazev2           obec2    ulice2  cislo_popisne2  \
0  Základní škola         Dobřany       NaN             2.0   
1  Mateřská škola  Hradec Králové  Sokolská           581.0   
2  Základní škola  Hradec Králové  Nerudova          1180.0   

   cislo_orientacni2        mestska_cast2     psc2 vyucovaci_jazyk2 kapacita2  \
0                NaN              Dobřany  51801.0              NaN       250   
1                NaN  Nový Hradec Králové  50003.0              NaN        30   
2               28.0    Pražské Předměstí  50002.0              NaN        70   

  platnost_zarizeni2          id3 typ3          nazev3           obec3  \
0             Platné  150048408.0  G21  Školní družina         Dobřany   
1             Platné  102078297.0  B00  Základní škola  Hradec Králové   
2             Platné  110011473.0  C00   Střední škola  Hradec Králové   

     ulice3  cislo_popisne3  cislo_orientacni3        mestska_cast3     psc3  \
0       NaN             2.0                NaN              Dobřany  51801.0   
1  Sokolská           581.0                NaN  Nový Hradec Králové  50003.0   
2   Lidická          1175.0                2.0    Slezské Předměstí  50002.0   

  vyucovaci_jazyk3 kapacita3 platnost_zarizeni3          id4 typ4  \
0              NaN        47             Platné  150048416.0  G22   
1              NaN        60             Platné  181106825.0  G22   
2              NaN        44             Platné  110011481.0  G21   

           nazev4           obec4    ulice4 cislo_popisne4  cislo_orientacni4  \
0     Školní klub         Dobřany       NaN            2.0                NaN   
1     Školní klub  Hradec Králové  Sokolská          581.0                NaN   
2  Školní družina  Hradec Králové  Nerudova         1180.0               28.0   

         mestska_cast4     psc4  vyucovaci_jazyk4 kapacita4  \
0              Dobřany  51801.0               NaN        66   
1  Nový Hradec Králové  50003.0               NaN        60   
2    Pražské Předměstí  50002.0               NaN        40   

  platnost_zarizeni4          id5 typ5          nazev5           obec5  \
0             Platné  110036751.0  L11  Školní jídelna         Dobřany   
1             Platné          NaN  NaN             NaN             NaN   
2             Platné  150061790.0  G22     Školní klub  Hradec Králové   

     ulice5  cislo_popisne5  cislo_orientacni5      mestska_cast5     psc5  \
0       NaN             2.0                NaN            Dobřany  51801.0   
1       NaN             NaN                NaN                NaN      NaN   
2  Nerudova          1180.0               28.0  Pražské Předměstí  50002.0   

   vyucovaci_jazyk5 kapacita5 platnost_zarizeni5          id6 typ6  \
0               NaN       220             Platné  181042096.0  A00   
1               NaN       NaN                NaN          NaN  NaN   
2               NaN        24             Platné  110011490.0  L11   

           nazev6           obec6    ulice6  

(2987, 117)


In [4]:
#json to csv

import json
import csv

# Load the JSON file
with open('kraje.json', 'r') as file:
    data = json.load(file)

# Define the CSV file to write to
csv_file = 'kraje.csv'

# Extract data for CSV
csv_data = []

for feature in data['features']:
    csv_entry = {
        "type": feature['type'],
        "nationalCode": feature['nationalCode'],
        "localId": feature['localId'],
        "name": feature['name'],
        "id": feature['id'],
        "geometry_type": feature['geometry']['type'],
        "coordinates": feature['geometry']['coordinates']
    }
    csv_data.append(csv_entry)

# Write to CSV
with open(csv_file, mode='w', newline='') as file:
    writer = csv.DictWriter(file, fieldnames=csv_data[0].keys())
    writer.writeheader()
    for row in csv_data:
        writer.writerow(row)

print(f"Data has been written to {csv_file}")



kraje = pd.read_csv("kraje.csv", sep=",")
display(kraje.shape)
display(kraje.head(2))

Data has been written to kraje.csv


In [3]:
!mkdir gps_souradnice_kraju

In [7]:
#jeden soubor pro jeden kraj
for i in range(kraje.shape[0]):
    with open (f"gps_souradnice_kraju/kraj{i}.txt", "w") as f:
        f.write(kraje.coordinates[i])

#.....................................
kraje["coordinates2"]="A"


#.....................................
#spojení všech tabulek dohromady a převedení souřadnic do vhodného tvaru
import glob

files = glob.glob("gps_souradnice_kraju/kraj*.txt")
files.sort(key=lambda x: int(x[len("gps_souradnice_kraju/kraj"):-len(".txt")]))  # Sort files by the numeric value in the filename

dfs = []
for file_path in files:
    with open(file_path, 'r') as file:
        raw_data = file.read()
        dfs.append(raw_data)

        
for i in range(14):
    cleaned_data = dfs[i].strip('\'"\n')

    # Add necessary brackets to ensure it's a valid list of lists
    if not cleaned_data.startswith('['):
        cleaned_data = '[' + cleaned_data
    if not cleaned_data.endswith(']'):
        cleaned_data = cleaned_data + ']'

    # Try parsing the corrected data string using json.loads
    try:
        data_list = json.loads(cleaned_data)
    except json.JSONDecodeError as e:
        print("JSON decoding error:", e)
        data_list = []

    # Check the type and structure of data_list again
    if isinstance(data_list, list) and data_list:
        # Flatten the list of lists into a list of tuples
        flat_list = [tuple(coord) for sublist in data_list for coord in sublist]

        # Create a pandas DataFrame from the list of tuples
        df = pd.DataFrame(flat_list, columns=['Longitude', 'Latitude'])

    else:
        print("Data parsing failed or resulted in an empty list.")


    zz = list(zip(df.Longitude, df.Latitude))
    kraje.at[i,"coordinates2"] = zz 

In [11]:
kraje

type  nationalCode   localId                  name            id  \
0   Feature            19   AU.2.19    Hlavní město Praha  CZ0100000000   
1   Feature            27   AU.2.27      Středočeský kraj  CZ0200000000   
2   Feature            35   AU.2.35        Jihočeský kraj  CZ0310000000   
3   Feature            43   AU.2.43         Plzeňský kraj  CZ0320000000   
4   Feature            51   AU.2.51      Karlovarský kraj  CZ0410000000   
5   Feature            60   AU.2.60          Ústecký kraj  CZ0420000000   
6   Feature            78   AU.2.78        Liberecký kraj  CZ0510000000   
7   Feature            86   AU.2.86  Královéhradecký kraj  CZ0520000000   
8   Feature            94   AU.2.94       Pardubický kraj  CZ0530000000   
9   Feature           108  AU.2.108         Kraj Vysočina  CZ0630000000   
10  Feature           116  AU.2.116     Jihomoravský kraj  CZ0640000000   
11  Feature           124  AU.2.124        Olomoucký kraj  CZ0710000000   
12  Feature           132  AU.2.132  Moravskoslezský kraj  CZ0800000000   
13  Feature           141  AU.2.141          Zlínský kraj  CZ0720000000   

   geometry_type                                        coordinates  \
0        Polygon  [[[14.528258, 49.999837], [14.528388, 49.99991...   
1        Polygon  [[[15.4973, 49.970052], [15.497103, 49.970144]...   
2        Polygon  [[[14.925793, 49.482316], [14.925835, 49.48235...   
3        Polygon  [[[12.580676, 49.90343], [12.580671, 49.903518...   
4        Polygon  [[[12.580676, 49.90343], [12.58078, 49.903426]...   
5        Polygon  [[[14.506469, 50.805714], [14.506475, 50.80569...   
6        Polygon  [[[14.506469, 50.805714], [14.506535, 50.80572...   
7        Polygon  [[[15.770877, 50.172756], [15.77088, 50.172782...   
8        Polygon  [[[15.770877, 50.172756], [15.770874, 50.17273...   
9        Polygon  [[[14.925793, 49.482316], [14.925787, 49.48226...   
10       Polygon  [[[15.99197, 49.03082], [15.990972, 49.031095]...   
11       Polygon  [[[17.217389, 49.838108], [17.217266, 49.83815...   
12       Polygon  [[[17.217389, 49.838108], [17.217391, 49.83810...   
13       Polygon  [[[17.17167, 49.082837], [17.172277, 49.082952...   

                                         coordinates2  
0   [(14.528258, 49.999837), (14.528388, 49.999912...  
1   [(15.4973, 49.970052), (15.497103, 49.970144),...  
2   [(14.925793, 49.482316), (14.925835, 49.482352...  
3   [(12.580676, 49.90343), (12.580671, 49.903518)...  
4   [(12.580676, 49.90343), (12.58078, 49.903426),...  
5   [(14.506469, 50.805714), (14.506475, 50.805694...  
6   [(14.506469, 50.805714), (14.506535, 50.80572)...  
7   [(15.770877, 50.172756), (15.77088, 50.172782)...  
8   [(15.770877, 50.172756), (15.770874, 50.17273)...  
9   [(14.925793, 49.482316), (14.925787, 49.482267...  
10  [(15.99197, 49.03082), (15.990972, 49.031095),...  
11  [(17.217389, 49.838108), (17.217266, 49.838154...  
12  [(17.217389, 49.838108), (17.217391, 49.838107...  
13  [(17.17167, 49.082837), (17.172277, 49.082952)...

In [33]:
kraje["stred"] = "A"


for i in range(14):
    polygon = Polygon(kraje.coordinates2[i])
    # Calculate the centroid of the polygon
    centroid = polygon.centroid
    # Get the coordinates of the centroid
    centroid_coordinates = (centroid.x, centroid.y)
    kraje.at[i,"stred"] = centroid_coordinates 

    
kraje["stred"] = kraje["stred"].apply(lambda x: (x[1], x[0]))

In [53]:
#pro streamlit aplikaci
for i in range(14):
    print(f"\"{kraje.loc[i,'name']}\": {list(kraje['stred'][i])},")

"Hlavní město Praha": [50.06678964987252, 14.465998829962977],
"Středočeský kraj": [50.003605191950115, 14.54954836371052],
"Jihočeský kraj": [49.09310368241909, 14.432286603192251],
"Plzeňský kraj": [49.59818612785983, 13.228010116617472],
"Karlovarský kraj": [50.1740783270064, 12.753140604283816],
"Ústecký kraj": [50.53040763516859, 13.84565561762281],
"Liberecký kraj": [50.70495750261212, 14.99864445395474],
"Královéhradecký kraj": [50.383626410733015, 15.866464780805817],
"Pardubický kraj": [49.90127803525259, 16.191215444747982],
"Kraj Vysočina": [49.41344724547589, 15.671506555415327],
"Jihomoravský kraj": [49.08016770385136, 16.635192353088943],
"Olomoucký kraj": [49.77734134610242, 17.19105583754125],
"Moravskoslezský kraj": [49.82068318540236, 17.979370693046423],
"Zlínský kraj": [49.22046625560532, 17.747374912706007],


In [13]:
celk_df = pd.read_csv("celk_df.csv", sep="#")
print(celk_df.shape)
print(celk_df.Coordinates.isna().sum())
celk_df = celk_df.dropna(subset=['Coordinates'])
celk_df['Coordinates'] = celk_df['Coordinates'].apply(eval)
celk_df['Coordinates'] = celk_df['Coordinates'].apply(lambda x: (x[1], x[0])) #přehození souřadnic

(2987, 117)
278


In [15]:
#Přiřazení školy ke kraji na základě GPS souřanic školy a hranic krajů
from shapely.geometry import Point, Polygon

# Sample data
df1 = kraje.loc[:,:]

# Adjusting df2 to have one point inside the polygon and one outside
df2 = celk_df.loc[:,:]

# Initialize the 'Region' column with empty strings or a default value
df2['Region'] = ''

# Define the function to check if a point is inside a polygon
def is_point_in_region(point, polygon):
    return polygon.contains(Point(point))

# Iterate through each region in df1
for i in range(14):
    # Define the polygon from df1 coordinates
    polygon_coords = df1['coordinates2'].iloc[i]
    polygon = Polygon(polygon_coords)
    
    # Apply the function to df2 and conditionally assign region name
    df2['Region'] = df2.apply(
        lambda row: df1.loc[i, 'name'] if is_point_in_region(row['Coordinates'], polygon) and row['Region'] == '' else row['Region'], 
        axis=1
    )

In [16]:
#kontrola
df2['Region']

1       Královéhradecký kraj
2       Královéhradecký kraj
3       Královéhradecký kraj
4       Královéhradecký kraj
5       Královéhradecký kraj
7       Královéhradecký kraj
8       Královéhradecký kraj
9       Královéhradecký kraj
10      Královéhradecký kraj
11      Královéhradecký kraj
12      Královéhradecký kraj
13      Královéhradecký kraj
14      Královéhradecký kraj
15      Královéhradecký kraj
16      Královéhradecký kraj
17      Královéhradecký kraj
18      Královéhradecký kraj
19      Královéhradecký kraj
20      Královéhradecký kraj
21      Královéhradecký kraj
22      Královéhradecký kraj
23      Královéhradecký kraj
25      Královéhradecký kraj
27      Královéhradecký kraj
28      Královéhradecký kraj
29      Královéhradecký kraj
30      Královéhradecký kraj
31      Královéhradecký kraj
32      Královéhradecký kraj
33      Královéhradecký kraj
34      Královéhradecký kraj
35      Královéhradecký kraj
36      Královéhradecký kraj
37      Královéhradecký kraj
38      Králov

In [17]:
df2['Coordinates'] = df2['Coordinates'].apply(lambda x: (x[1], x[0]))

In [18]:
df2.to_csv("celk_df_f.csv", index=False, sep="#", encoding="utf-8")

In [20]:
#kontrola
df2.head(3)

nazev  \
1  Základní škola a Mateřská škola při Fakultní n...   
2  Mateřská škola, základní škola a střední škola...   
3  PROINTEPO - Střední škola, Základní škola a Ma...   

                                              adresa       ico        izo  \
1  Sokolská 581, Nový Hradec Králové, 500 03 Hrad...  70837554  600023915   
2  Nerudova 1180/28, Pražské Předměstí, 500 02 Hr...  25262165  600023940   
3  Hrubínova 1458/1, Pražské Předměstí, 500 02 Hr...  25263633  600023958   

                 reditel                   pravni_forma  \
1  Mgr. Blanka Kovandová         příspěvková organizace   
2    Mgr. Monika Bourová  společnost s ručením omezeným   
3   Mgr. Miriam Urbanová  společnost s ručením omezeným   

                                          zrizovatel        id2 typ2  \
1  Královéhradecký kraj, Pivovarské náměstí 1245/...  102754713  A00   
2                                        Není uveden   48162485  B00   
3                                        Není uveden  110032349  A00   

           nazev2           obec2     ulice2  cislo_popisne2  \
1  Mateřská škola  Hradec Králové   Sokolská           581.0   
2  Základní škola  Hradec Králové   Nerudova          1180.0   
3  Mateřská škola  Hradec Králové  Hrubínova          1458.0   

   cislo_orientacni2        mestska_cast2     psc2 vyucovaci_jazyk2 kapacita2  \
1                NaN  Nový Hradec Králové  50003.0              NaN        30   
2               28.0    Pražské Předměstí  50002.0              NaN        70   
3                1.0    Pražské Předměstí  50002.0              NaN        21   

  platnost_zarizeni2          id3 typ3          nazev3           obec3  \
1             Platné  102078297.0  B00  Základní škola  Hradec Králové   
2             Platné  110011473.0  C00   Střední škola  Hradec Králové   
3             Platné   61223174.0  B00  Základní škola  Hradec Králové   

      ulice3  cislo_popisne3  cislo_orientacni3        mestska_cast3     psc3  \
1   Sokolská           581.0                NaN  Nový Hradec Králové  50003.0   
2    Lidická          1175.0                2.0    Slezské Předměstí  50002.0   
3  Hrubínova          1458.0                1.0    Pražské Předměstí  50002.0   

  vyucovaci_jazyk3 kapacita3 platnost_zarizeni3          id4 typ4  \
1              NaN        60             Platné  181106825.0  G22   
2              NaN        44             Platné  110011481.0  G21   
3              NaN        58             Platné  110032365.0  G12   

                       nazev4           obec4     ulice4 cislo_popisne4  \
1                 Školní klub  Hradec Králové   Sokolská          581.0   
2              Školní družina  Hradec Králové   Nerudova         1180.0   
3  Stanice zájmových činností  Hradec Králové  Hrubínova         1458.0   

   cislo_orientacni4        mestska_cast4     psc4  vyucovaci_jazyk4  \
1                NaN  Nový Hradec Králové  50003.0               NaN   
2               28.0    Pražské Předměstí  50002.0               NaN   
3                1.0    Pražské Předměstí  50002.0               NaN   

    kapacita4 platnost_zarizeni4          id5 typ5          nazev5  \
1          60             Platné          NaN  NaN             NaN   
2          40             Platné  150061790.0  G22     Školní klub   
3  neuvádí se             Platné  110032357.0  G21  Školní družina   

            obec5     ulice5  cislo_popisne5  cislo_orientacni5  \
1             NaN        NaN             NaN                NaN   
2  Hradec Králové   Nerudova          1180.0               28.0   
3  Hradec Králové  Hrubínova          1458.0                1.0   

       mestska_cast5     psc5  vyucovaci_jazyk5 kapacita5 platnost_zarizeni5  \
1                NaN      NaN               NaN       NaN                NaN   
2  Pražské Předměstí  50002.0               NaN        24             Platné   
3  Pražské Předměstí  50002.0               NaN        16             Platné   

           id6 typ6                          

In [19]:
from matplotlib import cm, colors

# Generate a list of unique colors
unique_zrizovatel = df2['zrizovatel_dropdown'].unique()
colormap = cm.get_cmap('tab10', len(unique_zrizovatel))  # Use a colormap with a sufficient number of unique colors
color_list = [colors.rgb2hex(colormap(i)[:3]) for i in range(len(unique_zrizovatel))]

# Map each zrizovatel to a color
zrizovatel_color_map = dict(zip(unique_zrizovatel, color_list))

# Initialize the map centered around the first address
map_center = df2['Coordinates'].iloc[0]
map = folium.Map(location=map_center, zoom_start=13)

# Add points to the map with different colors
for index, row in df2.iterrows():
    popup_content = folium.Popup(row['nazev'], max_width=300)  # Set the max_width as needed
    folium.CircleMarker(
        location=row['Coordinates'],
        radius=4,  # Adjust the radius as needed
        popup=popup_content,
        color=zrizovatel_color_map[row['zrizovatel_dropdown']],  # Border color
        fill=True,
        fill_color=zrizovatel_color_map[row['zrizovatel_dropdown']],  # Fill color
        fill_opacity=1  # Adjust the fill opacity as needed
    ).add_to(map)

# Save the map to an HTML file
#map.save("address_map.html")

# Display the map in Jupyter Notebook (if using Jupyter)
map
